# Sistema de Compressão

$ \frac{d\dot{m}}{dt} = \frac{A_1}{L_C}(\phi (N(t), \dot{m})P_1 - P_P(t)) $

$ \frac{d P_P}{dt} = \frac{C_1^2}{\nu _P}(\dot{m}(t) - \alpha (t) K_\nu \sqrt{P_P - P_{out}}) $

$ \begin{matrix} A_1 & = & 2.6\centerdot 10^{-3} m² \\
\nu _P & = & 2.0 m³ \\
L_C & = & 2.0 m \\
K_\nu & = & \frac{0.38 kg}{(kPa)^{0.5}s} \\
P_1 & = & 4.5 MPa \\
P{out} & = & 5.0 MPa \end{matrix}
$

$ \frac{d\dot{m}}{dt} = \frac{2.6\centerdot 10^{-3}}{2.0}(\phi (N(t), \dot{m})\centerdot 4.5 - P_P) $

$ \frac{d P_P}{dt} = \frac{479.029^2}{2.0}(\dot{m} - \alpha {0.38} \sqrt{P_P - 5.0}) $

#### Importações

In [3]:
import numpy as np
from scipy.optimize import fsolve
import casadi as ca
import plotly.graph_objects as go
import optuna
from plotly.subplots import make_subplots
import time
import matplotlib.pyplot as plt
import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import DataLoader, TensorDataset
import pandas as pd
from scipy.interpolate import griddata


c:\Users\guiar\AppData\Local\Programs\Python\Python312\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


#### Classes

##### Solução Numérica

In [76]:
class Simulation:
    def __init__(self, A1, Lc, kv, P1, P_out, C, alphas, N_RotS, nAlphas, nData, perturb,tempo, dt,file_path, decimal=','):
        self.A1 = A1
        self.Lc = Lc
        self.kv = kv
        self.P1 = P1
        self.P_out = P_out
        self.C = C
        self.alphas = alphas
        self.N_RotS = N_RotS
        self.nAlphas = nAlphas
        self.nData = nData
        self.perturb = perturb
        self.dt = dt
        self.tempo = tempo
        
        #Interpolação
        self.file_path = file_path
        self.decimal = decimal
        self.data = None
        self.N_rot = None
        self.Mass = None
        self.Phi = None

        self.interval = [np.linspace(i * self.tempo, (i + 1) * self.tempo, self.nData) for i in range(self.nAlphas)]
        self.time = 0
        
        self.alpha_values = []
        self.N_values = []
        self.massFlowrate = []
        self.PlenumPressure = []
        self.Phi_values = []
        self.RNN_train = []
        self.RNN_trainFut = []
        
    def load_data(self):
        self.data = pd.read_csv(self.file_path, decimal=self.decimal)
        
        self.N_rot = np.arange(2e4,6e4,1e3) # Vai de 20000hz até 60000hz, Shape: (40,)
        self.Mass = np.arange(3,21.1,0.1) # Vai de 3 até 21, Shape: (181,)
        self.Phi = self.data.values # Valores da tabela, Shape: (40,181)
    
    def interpolate(self, num_points=100):
        # Criar uma malha densa para interpolação
        phi_flat = self.Phi.ravel(order='F')
        lut = ca.interpolant('name','bspline',[self.N_rot, self.Mass],phi_flat)

        return lut

    def fun(self, variables, alpha, N):
        (x, y) = variables  # x e y são escalares
        phi_value = float(self.interpolate(num_points=100)([N, x]))  # Garantir que phi_value é escalar
        eqn_1 = (self.A1 / self.Lc) * ((phi_value * self.P1) - y) * 1e3
        eqn_2 = (self.C**2) / 2 * (x - alpha * self.kv * np.sqrt(y * 1000 - self.P_out * 1000))
        return [eqn_1, eqn_2]


    def run(self):
        self.load_data()
        lut = self.interpolate()
        # Condições iniciais
        result = fsolve(self.fun, (10, 10), args=(self.alphas[0],self.N_RotS[0]))
        print(result)
        init_m, init_p = result

        # Variáveis CasADi
        x = ca.MX.sym('x', 2)
        p = ca.MX.sym('p', 2)  # Parâmetros (alpha e N)
        alpha, N = p[0], p[1]  # Divisão dos parâmetros

        # Solução Numérica
        tm1 = time.time()
        for i in range(self.nAlphas):
            alpha_value = self.alphas[i] + np.random.normal(0, self.perturb, self.nData)
            N_value = self.N_RotS[i] + np.random.normal(0, 100, self.nData)
            self.alpha_values.append(alpha_value)
            self.N_values.append(N_value)

            rhs = ca.vertcat((self.A1 / self.Lc) * ((lut(ca.vertcat(N, x[0])) * self.P1) - x[1]) * 1e3,
                             (self.C**2) / 2 * (x[0] - alpha * self.kv * np.sqrt(x[1] * 1000 - self.P_out * 1000)))
            
            ode = {'x': x, 'ode': rhs, 'p': p}

            F = ca.integrator('F', 'cvodes', ode, self.interval[0][0],self.dt)

            for j in range(self.nData):
                params = [alpha_value[j], N_value[j]]
                sol = F(x0=[init_m, init_p], p=params)
                xf_values = np.array(sol["xf"])
                aux1, aux2 = xf_values
                self.massFlowrate.append(aux1)
                self.PlenumPressure.append(aux2)
                self.Phi_values.append(lut(ca.vertcat(N_value[j], aux1)))
                init_m = aux1[-1]
                init_p = aux2[-1]
                self.RNN_train.append([aux1[0], aux2[0], alpha_value[j], N_value[j]])
                self.RNN_trainFut.append([aux1[0], aux2[0], alpha_value[j], N_value[j]])

        tm2 = time.time()
        self.time = tm2-tm1
        self.massFlowrate = np.reshape(self.massFlowrate, [self.nAlphas, self.nData])
        self.PlenumPressure = np.reshape(self.PlenumPressure, [self.nAlphas, self.nData])
        self.Phi_values = np.reshape(self.Phi_values, [self.nAlphas, self.nData])


##### Interpolador

In [8]:
class DataInterpolatorCasadi:
    def __init__(self, file_path, decimal=','):
        self.file_path = file_path
        self.decimal = decimal
        self.data = None
        self.N_rot = None
        self.Mass = None
        self.Phi = None

    def load_data(self):
        self.data = pd.read_csv(self.file_path, decimal=self.decimal)
        
        self.N_rot = np.arange(2e4,6e4,1e3) # Vai de 20000hz até 60000hz, Shape: (40,)
        self.Mass = np.arange(3,21.1,0.1) # Vai de 3 até 21, Shape: (181,)
        self.Phi = self.data.values # Valores da tabela, Shape: (40,181)
        print("Dados carregados com sucesso.")
        print("Dimensão de N_rot:", self.N_rot.shape)
        print("Dimensão de Mass:", self.Mass.shape)
        print("Dimensão de Phi:", self.Phi.shape)

    def interpolate(self, num_points=100):
        # Criar uma malha densa para interpolação
        N_dense = np.linspace(self.N_rot.min(), self.N_rot.max(), num_points)
        Mass_dense = np.linspace(self.Mass.min(), self.Mass.max(), num_points)
        phi_flat = self.Phi.ravel(order='F')

        lut = ca.interpolant('name','bspline',[self.N_rot, self.Mass],phi_flat)

        # Calcular a malha de Z usando os pontos interpolados
        Phi_dense = np.zeros((num_points, num_points))
        for i, x in enumerate(N_dense):
            for j, y in enumerate(Mass_dense):
                Phi_dense[i, j] = lut([x, y])

        print("Dimensão de Phi_dense:", Phi_dense.shape)
        return N_dense, Mass_dense, Phi_dense, lut

    def plot_results(self, N_dense, Mass_dense, Phi_dense,x_test,y_test,z_interpolado):
        """Plota os resultados da interpolação e da amostra original."""
        fig, (ax1, ax2) = plt.subplots(1, 2, subplot_kw={'projection': '3d'}, figsize=(12, 6))

        # Dados Originais (Amostra)
        X_grid, Y_grid = np.meshgrid(self.Mass, self.N_rot) # EU REALMENTE NAO SEI COMO EU ENTRO COM 181,40 E O MESHGRID SAI COMO 40,181
        print(X_grid.shape,Y_grid.shape)
        ax1.scatter(X_grid, Y_grid, self.Phi,c=self.Phi.ravel(), cmap='viridis', edgecolor='k')
        ax1.set_title("Dados Originais (Amostra)")
        ax1.set_xlabel("Vazão")
        ax1.set_ylabel("N")
        ax1.set_zlabel("Phi")

        # Superfície Interpolada
        X_dense_grid, Y_dense_grid = np.meshgrid(Mass_dense, N_dense)
        ax2.plot_surface(X_dense_grid, Y_dense_grid, Phi_dense, cmap='viridis')
        ax2.set_title("Superfície Interpolada (CasADi)")
        ax2.set_xlabel("Vazão")
        ax2.set_ylabel("N")
        ax2.set_zlabel("Phi")

        ax2.scatter(y_test,x_test,z_interpolado, c = 'black')

        plt.show()

##### Modelo de Rede Neural

In [9]:
class MyModel(nn.Module):
    def __init__(self, units, A1, Lc, kv, P1, P_out, C, dt, x_min, x_max):
        self.A1 = A1
        self.Lc = Lc
        self.kv = kv
        self.P1 = P1
        self.P_out = P_out
        self.C = C
        self.dt = dt
        self.x_min = x_min
        self.x_max = x_max
        super(MyModel, self).__init__()
        
        # Camada de entrada
        self.input_layer = nn.Linear(3, 3)
        
        # Camadas RNN
        self.rnn_layers = nn.ModuleList([
            nn.LSTM(input_size=3, hidden_size=units, batch_first=True, bidirectional=True, bias= True)
        ])
        self.rnn_layers.append(nn.LSTM(input_size=units*2, hidden_size=units, batch_first=True, bias= True))
        
        # Camada densa
        self.dense = nn.Linear(units, 2)

        # Inicialização dos pesos com Xavier (Glorot Uniform)
        self._initialize_weights()

    def _initialize_weights(self):
        # Inicializador Xavier (Glorot) nos pesos das camadas RNN
        for rnn_layer in self.rnn_layers:
            for name, param in rnn_layer.named_parameters():
                if 'weight' in name:
                    nn.init.xavier_uniform_(param)
                elif 'bias' in name:
                    nn.init.zeros_(param)

        nn.init.xavier_uniform_(self.dense.weight)
        nn.init.zeros_(self.dense.bias)

    def forward(self, inputs):
        # Passagem pelas camadas RNN
        rnn_output = 2 * (inputs - self.x_min) / (self.x_max - self.x_min) - 1
        for rnn_layer in self.rnn_layers:
            rnn_output, _ = rnn_layer(rnn_output)
            rnn_output = torch.tanh(rnn_output)  # Aplicando tanh explicitamente após cada camada RNN
         # Pegando apenas a última saída da sequência e desnormalizando
        dense_output = self.dense(rnn_output[:, -1, :])  # Dimensão [batch_size, hidden_size * num_directions]
        
        desnormalizado = ((dense_output + 1) / 2) * (self.x_max[:, :, :2] - self.x_min[:, :, :2]) + self.x_min[:, :, :2]
          # Pegando apenas a última saída da sequência
        return desnormalizado
    
    def loss_custom(self, y_true, y_pred, inputs):
        # Implementação da função de perda
        m_t = (11* y_pred[:, :, 0] - 18 *inputs[:, -2, 0] + 9 * inputs[:, -3, 0] - 2 * inputs[:, 0, 0])/6*self.dt
        p_t = (11* y_pred[:, :, 1] - 18 *inputs[:, -2, 1] + 9 * inputs[:, -2, 1] - 2 * inputs[:, -2, 1])/6*self.dt
        fLoss_mass = torch.mean(torch.square(m_t - (self.A1/self.Lc)*((1.5 * self.P1) - y_pred[:, :, 1]) * 1e3))
        fLoss_pres = torch.mean(torch.square(p_t - (self.C**2)/2 * (y_pred[:, :, 0] - inputs[:, -1, -1]* self.kv * torch.sqrt((torch.abs(y_pred[:, :, 1] * 1000 - self.P_out * 1000))))))
        phys_loss = fLoss_mass + fLoss_pres
        data_loss =  torch.mean((y_true[:, 0, 0] - y_pred[:, :, 0]) ** 2) + torch.mean((y_true[:, 0, 1] - y_pred[:, :, 1]) ** 2)
        return data_loss +  1e-11*phys_loss

    def train_model(self, model, train_loader, lr, epochs, optimizers):
        optimizer = optimizers(model.parameters(), lr=lr)
        model.train()
        
        for epoch in range(epochs):
            total_loss = 0
            for inputs, y_true in train_loader:
                optimizer.zero_grad()
                
                y_pred = model(inputs)
                loss = self.loss_custom(y_true, y_pred, inputs)
                loss.backward()
                optimizer.step()
                
                total_loss += loss.item()
            print(f"Epoch [{epoch+1}/{epochs}], Loss: {total_loss / len(train_loader)}")
            
    def test_model(self, x_test, interval, model):
        model.eval()
        massFlowrate100 = [x_test[0, 0, 0].item(), x_test[0, 1, 0].item(), x_test[0, 2, 0].item()]
        PlenumPressure100 = [x_test[0, 0, 1].item(), x_test[0, 1, 1].item(), x_test[0, 2, 1].item()]

        # Preparar o tensor inicial fora do loop
        input_tensor = torch.zeros((1, 3, 3), dtype=torch.float32)

        # Loop de previsões
        tm1 = time.time()
        for i in range(len(interval)):
            # Atualizar os valores do tensor diretamente
            input_tensor[0, :, 0] = torch.tensor(massFlowrate100[-3:])
            input_tensor[0, :, 1] = torch.tensor(PlenumPressure100[-3:])
            input_tensor[0, :, 2] = x_test[i, :, 2]

            # Previsão com desativação do gradiente
            with torch.no_grad():
                prediction100 = model(input_tensor)

            # Adicionar previsões diretamente
            massFlowrate100.append(prediction100[0, 0, 0].item())
            PlenumPressure100.append(prediction100[0, 0, 1].item())
        tm2 = time.time()
        timeteste = tm2 - tm1
        model.train()
        return massFlowrate100, PlenumPressure100, timeteste

#### Constantes e Variáveis Auxiliares

In [77]:
np.random.seed(42)
print(np.random.seed)

# Constantes
A1 = (2.6)*(10**-3)
Lc = 2
kv = 0.38
P1 = 4.5
P_out = 5
C = 479

timestep = 3 # Passos no passado para prever o próximo
nAlphas = 5 # Número de vezes que o Alfa irá mudar, considere o treino e os testes.
alphas = np.random.uniform(0.35,0.65, nAlphas+1) # Abertura da válvula
N_RotS = np.random.uniform(27e3, 6e4, nAlphas+1)
epochs = 100
nData = 600
nDataTeste = nData//nAlphas
perturb = 1e-4
tempo = 60
dt = 0.1 # Tempo amostral

# Variáveis auxiliares
interval = [np.linspace(i * tempo, (i + 1) * tempo, nData) for i in range(nAlphas)]
interval_test = [np.linspace(i * tempo, (i + 1) * tempo, nDataTeste) for i in range(nAlphas)]
massFlowrate = []
PlenumPressure = []
alpha_values = []
RNN_train = []
RNN_trainFut = []

<built-in function seed>


### Solução Numérica

##### Interpolador

In [5]:
interpol = DataInterpolatorCasadi('/home/guilhermefreire/UFBA/Iniciação Científica/Sistema de Compressão/tabela_phi.csv')
interpol.load_data()
interpolant_func = interpol.interpolate(num_points=100)[3]

# Testa a função de interpolação
N_rot_test = 30000
MassInterpol_test = 15
Phi_interpolado = interpolant_func([N_rot_test, MassInterpol_test])
print(f"Valor interpolado em (x={N_rot_test}, y={MassInterpol_test}):", Phi_interpolado)

NameError: name 'DataInterpolatorCasadi' is not defined

##### Cálculo da Solução

In [78]:
# Crie uma instância da classe Simulation
sim = Simulation(A1, Lc, kv, P1, P_out, C, alphas, N_RotS, nAlphas, nData, perturb, tempo, dt, 'E:/Faculdade/UFBA/UFBA/Iniciação Científica/Sistema de Compressão/tabela_phi.csv')
sim.load_data()
# Execute a simulação
sim.run()

RNN_train = sim.RNN_train
RNN_trainFut = sim.RNN_trainFut
massFlowrate = sim.massFlowrate
PlenumPressure = sim.PlenumPressure
alpha_values = sim.alpha_values
phi_values = sim.Phi_values

print(sim.time)

[4.58815777 5.68193842]
0.6710898876190186


##### Gráfico do Modelo

In [82]:
fig = make_subplots(rows=2, cols=2, subplot_titles=("Vazão vs Tempo", "Pressão vs Tempo", "Alpha vs Tempo", "Phi vs Tempo"))

for i in range(0, nAlphas):
    # Vazão
    fig.add_trace(go.Scatter(x=interval[i], y=np.squeeze(massFlowrate[i]), mode='lines',
                             name='Vazão', legendgroup='massflow', showlegend=i == 0), row = 1, col = 1)
    # Pressão
    fig.add_trace(go.Scatter(x=interval[i], y=np.squeeze(PlenumPressure[i]), mode='lines',
                             name='Pressão', legendgroup='pressure', showlegend=i == 0), row = 1, col = 2)
    # Alphas
    fig.add_trace(go.Scatter(x=interval[i], y=np.squeeze(alpha_values[i]), mode='lines', 
                             name='Alphas', line=dict(dash='dash'), legendgroup='alpha', showlegend=i == 0), row = 2, col = 1)
    # Phi
    fig.add_trace(go.Scatter(x=interval[i], y=np.squeeze(phi_values[i]), mode='lines', 
                             name='Alphas', line=dict(dash='dash'), legendgroup='alpha', showlegend=i == 0), row = 2, col = 2)

# Atualiza layout
fig.update_layout(
    xaxis_title='Tempo',
    grid=dict(rows=1, columns=3),
    template='plotly',
    showlegend=False,
    height = 600
)

# Mostra a figura
fig.show()


### Rede Neural

##### Dados de Treino

In [37]:
RNN_train = np.array(RNN_train)


X_train = []
y_train = []

for i in range(len(RNN_train) - timestep):
    X_train.append(RNN_train[i:i + timestep])  
    if i + timestep < len(RNN_train):           
        y_train.append(RNN_train[i + timestep, :2])  

X_train = torch.tensor(X_train, dtype=torch.float32)
y_train = torch.tensor(y_train, dtype=torch.float32)

x_min = X_train.amin(dim=(0, 1), keepdim=True)
x_max = X_train.amax(dim=(0, 1), keepdim=True)

y_train = y_train.unsqueeze(1)

##### Rede

##### Treinamento

In [38]:
model = MyModel(50, A1, Lc, kv, P1, P_out, C, dt, x_min, x_max)

train_dataset = TensorDataset(X_train, y_train)
train_loader = DataLoader(train_dataset, batch_size= 32, shuffle=True)
Adam = optim.Adam
model.train_model(model, train_loader, 1e-5, epochs, Adam)

Epoch [1/100], Loss: 1.8107676020563284
Epoch [2/100], Loss: 1.3139092712514182
Epoch [3/100], Loss: 0.7360311116872311
Epoch [4/100], Loss: 0.24080080622390135
Epoch [5/100], Loss: 0.03848780426425117
Epoch [6/100], Loss: 0.009836110064009232
Epoch [7/100], Loss: 0.006579696519502889
Epoch [8/100], Loss: 0.005431342879925837
Epoch [9/100], Loss: 0.004641706876552054
Epoch [10/100], Loss: 0.0040045488729520936
Epoch [11/100], Loss: 0.0035136566484478046
Epoch [12/100], Loss: 0.003169313491781804
Epoch [13/100], Loss: 0.002925597045988615
Epoch [14/100], Loss: 0.0027624351532334513
Epoch [15/100], Loss: 0.002632959483207257
Epoch [16/100], Loss: 0.0025122126897991594
Epoch [17/100], Loss: 0.0023869558535729732
Epoch [18/100], Loss: 0.002255351324667479
Epoch [19/100], Loss: 0.00214931529432561
Epoch [20/100], Loss: 0.0019840559187612786
Epoch [21/100], Loss: 0.0018538328916279238
Epoch [22/100], Loss: 0.0017307713627163668
Epoch [23/100], Loss: 0.0016135464153768345
Epoch [24/100], Loss

##### Dados de teste

In [39]:
massFlowrateTeste = []
PlenumPressureTeste = []
RNN_test = []
x_test = []
alpha_valuesTeste = []
aux1 = []
aux2 = []
interval3 = np.linspace(0, tempo*nAlphas, len(train_dataset))
alphasTeste = np.random.uniform(0.35,0.65, nAlphas) # Abertura da válvula

sim = Simulation(A1, Lc, kv, P1, P_out, C, alphasTeste, nAlphas, nData, perturb, tempo, dt)

sim.run()

RNN_test = sim.RNN_train
massFlowrateTeste = sim.massFlowrate
PlenumPressureTeste = sim.PlenumPressure
alpha_valuesTeste = sim.alpha_values
print(sim.time)

RNN_test = np.array(RNN_test)

for i in range(len(RNN_test) - 3):
    x_test.append(RNN_test[i:i + 3])

x_test = torch.tensor(x_test, dtype=torch.float32)

massFlowrateTeste = np.array(massFlowrateTeste)
PlenumPressureTeste = np.array(PlenumPressureTeste)

4.329961776733398


##### Gráfico Rede Neural

In [40]:
fig = make_subplots(rows=1, cols=2, subplot_titles=("Mass Flow Rate vs Time", "Plenum Pressure vs Time"))

tm1 = time.time()
# Colocando o modelo em modo de avaliação

# Supondo que x_test já esteja definido e seja um tensor PyTorch
with torch.no_grad():  
    prediction = model(x_test)

mass = prediction[:, :, 0]
pressure = prediction[:, :, 1]

mass = mass.detach().numpy()
pressure = pressure.detach().numpy()

tm2 = time.time()
print(tm2-tm1)

fig.add_trace(go.Scatter(x=interval3,y=np.squeeze(mass),mode='lines',
                                line=dict(dash='solid')),row=1, col=1)
fig.add_trace(go.Scatter(x=interval3,y=np.squeeze(pressure),mode='lines',
                                line=dict(dash='solid')),row=1, col=2)


for i in range(nAlphas):
    # Modelo
    fig.add_trace(go.Scatter(x=np.squeeze(interval_test[i]), y=np.squeeze(massFlowrateTeste[i]), mode='lines',name='Model Mass Flow Rate', line=dict(dash='dash', color='red')),
                  row=1, col=1)
    fig.add_trace(go.Scatter(x=np.squeeze(interval_test[i]), y=np.squeeze(PlenumPressureTeste[i]), mode='lines', name= 'Model Plenum Pressure', line=dict(dash='dash', color='red')),
                  row=1, col=2)

fig.update_layout(
    title='Resultados Rede Neural',
    xaxis_title='Time',
    yaxis_title='Value',
    template='plotly',
    showlegend=False
)
fig.show()


0.08506560325622559


In [41]:
massFlowrate100, PlenumPressure100,time2 = model.test_model(x_test, interval3, model)
print(time2)

4.444951295852661


In [42]:
fig3 = make_subplots(rows=1, cols=2, subplot_titles=("Mass Flow Rate vs Time", "Plenum Pressure vs Time"))

fig3.add_trace(go.Scatter(x=interval3,y=np.squeeze(massFlowrate100),mode='lines',
                                line=dict(dash='solid')),row=1, col=1)
fig3.add_trace(go.Scatter(x=interval3,y=np.squeeze(PlenumPressure100),mode='lines',
                                line=dict(dash='solid')),row=1, col=2)

for i in range(nAlphas):
    # Modelo
    fig3.add_trace(go.Scatter(x=np.squeeze(interval_test[i]), y=np.squeeze(massFlowrateTeste[i]), mode='lines',name='Model Mass Flow Rate', line=dict(dash='dash', color='red')),
                  row=1, col=1)
    fig3.add_trace(go.Scatter(x=np.squeeze(interval_test[i]), y=np.squeeze(PlenumPressureTeste[i]), mode='lines', name= 'Model Plenum Pressure', line=dict(dash='dash', color='red')),
                  row=1, col=2)

fig3.update_layout(
    title='Resultados Rede Neural',
    xaxis_title='Time',
    yaxis_title='Value',
    template='plotly',
    showlegend=False
)
fig3.show()